In [1]:
from math import *
import os, aa, rec
import ROOT

from ipywidgets import interact, interactive, fixed, interact_manual, Output, VBox, HBox
import ipywidgets as widgets
import IPython
from IPython.display import clear_output, display
from array import array
from ctypes import string_at
from copy import copy

loading root....  /opt/root_build
Welcome to JupyROOT 6.19/01
loading /home/anders/aanet/lib/libaaevt.so ... ok (0.03 s.)
loading /home/anders/aanet/lib/libaastro.so ... ok (0.00 s.)
 welcome to aanet v2.1.0-266-gaab783c
loading /home/anders/aanet/lib/aarec.so ... ok (0.01 s.)


In [2]:
# If you don't already have the pdf-data files, get them from Lyon with
# cp username@cca7.in2p3.fr:/pbs/throng/km3net/src/Jpp/trunk/data/J*p.dat datadir

datadir = os.environ['JPP_DIR']+'/data/'
track_files = [ datadir + 'J%dp.dat'% n for n in range( 1,7)]
shower_files = [datadir + 'J14p.dat',  datadir + 'J13p.dat']
aa_shower_file = ["/sps/km3net/users/heijboer/he/output/genhen_JUNE_2___.hist.root"]

In [3]:
#Load in PDFs
jpp_shower_pdf = ROOT.JppShowerPdf( *shower_files )
jpp_shower_npe = ROOT.JppShowerNpe( jpp_shower_pdf )
del jpp_shower_pdf

aa_shower_pdf  = ROOT.DigitalShowerPdf()
aa_shower_pdf.init()

loaded /home/anders/jpp/data/J14p.dat
loaded /home/anders/jpp/data/J13p.dat
Added 
Blurring PDF
Constructed JppShowerPdf.


In [4]:
def get_aa_npe(E, D, cd, cos_pmt): #energy in PeV
    F = getattr(aa_shower_pdf, 'get_h3_value')
    return F(aa_shower_pdf.H3, D, cd, cos_pmt ) * E

color_scheme = {
    "jpp":            [ 1, 34],
    "jpp_shower_max": [ 209, 211],
    "jpp_elongated":  [97, 93],
    "aanet":          [65, 65],
}
color_scheme["j"] = color_scheme["o"] = color_scheme["jpp"] #j for jpp, o for original
color_scheme["s"] = color_scheme["c"] = color_scheme["jpp_shower_max"] #s for shower max, c for corrected
color_scheme["e"] = color_scheme["jpp_elongated"] #e for elongated
color_scheme["a"] = color_scheme["aanet"]
    
def get_color( pdf_string, table = color_scheme):    
    return table[pdf_string]

In [14]:
def fill_histograms( Fs, histlist, b, quantity, qvals, pdf_infos, logE, D, cd, smax_coord ):
    iq = histlist[0].GetBinCenter(b)

    new_D  = copy(D)
    new_cd = copy(cd)
    if smax_coord: #treat D_s, cd_s and iq, as if coordinates to shower max, and perform transformations from that frame.
        D_s  = copy(D)
        cd_s = copy(cd)
        if   quantity == "cd":
            new_D  = ROOT.get_vertex_D ( D_s, iq, 10**logE )
            iq     = ROOT.get_vertex_cd( D_s, iq,  10**logE )
        elif quantity == "D" :    
            new_cd = ROOT.get_vertex_cd( iq, cd_s, 10**logE )
            iq     = ROOT.get_vertex_D ( iq, cd_s, 10**logE )

    if quantity == "E" and logx: iq = 10**iq

    for ipdf, pdf in enumerate(pdf_infos):
        this_args = list(pdf[2])

        this_args[1]        = new_D
        this_args[2]        = new_cd
        this_args[qvals[0]] = iq

        if pdf[3] == 1:
            histlist[ipdf*pdf_infos[0][3]].SetBinContent(b, Fs[ipdf]( *this_args ))
        else:
            for icomp in range(pdf[3]):
                histlist[ipdf*pdf_infos[0][3] + icomp].SetBinContent(b, Fs[ipdf](icomp, *this_args))
                print(Fs[ipdf](icomp, *this_args))
                print( "args:", *this_args)

In [17]:
def plot_pdf(pdf0 = "aanet",
             pdf1 = "jpp_elongated",
             quantity = "cd",
             smax_coord = False,
             logE=6,
             D=100,
             cd=0.8,
             cos_pmt=-0.8,
             nbins = 200,
             logy = False, logx = False,
             x0 = -1.0, x1 = 1.0,
             logy0 =  0.0, logy1 = 0.0, 
             steps =  10,
             elong_steps = 10):
        
    args_A = ( 10**(logE - 6), D, cd, cos_pmt )
    args   = ( 10**logE,       D, cd, cos_pmt, steps )
    args_S = ( 10**logE,       D, cd, cos_pmt, steps )
    args_E = ( 10**logE,       D, cd, cos_pmt, steps, elong_steps )

    pdf_info_dic = {"jpp":            ("jpp",            getattr(*( jpp_shower_npe, 'npe'   )), args,   3, "Jpp 4d"),
                    "jpp_shower_max": ("jpp_shower_max", getattr(*( jpp_shower_npe, 'npe_S' )), args_S, 3, "Jpp 4d_{shower max.}"),
                    "jpp_elongated":  ("jpp_elongated",  getattr(*( jpp_shower_npe, 'npe_E' )), args_E, 3, "Jpp 4d_{E elong.}"),
                    "aanet":          ("aanet",          get_aa_npe,                            args_A, 1, "Aanet 3d")
                    }
    pdf_infos = [ pdf_info_dic[pdf0], pdf_info_dic[pdf1] ]
    
    Fs        = [ pdf_infos[0][1],    pdf_infos[1][1]    ]
    
    #[index, mint, maxt, xlabel]
    qvals = { 'E'       : [0,[10**(9*x0), 9*x0][logx], [10**(9*x1), 9*x1][logx], [0.1, 0.6, 0.45, 0.9],['E [GeV]', 'log(E) [GeV]'][logx]],
              'D'       : [1, 10**x0, 10**(3*x1), [0.5, 0.6, 0.9 , 0.9],['D [m]', 'D_{shower max} [m]'][smax_coord]],
              'cd'      : [2, x0,      x1, [0.1, 0.6, 0.45, 0.9],['cos(#theta)', 'cos(#theta_{shower max})'][smax_coord]],
              'cos_pmt' : [3, x0,      x1, [0.5, 0.6, 0.9 , 0.9],'cos(#theta_{PMT})']
    }[quantity]

    histlist = [ ROOT.TH1D("h"+str(i),\
                           "Comparison of "+pdf_infos[0][4]+" and "+pdf_infos[1][4]+";"+qvals[-1]+";<n.p.e.>",\
                           nbins,\
                           qvals[1],\
                           qvals[2]) for i in range( pdf_infos[0][3] + pdf_infos[1][3] ) ]
    
    for b in range(1, histlist[0].GetNbinsX()+1):
        fill_histograms( Fs, 
                         histlist,
                         b,
                         quantity,
                         qvals,
                         pdf_infos,
                         logE,
                         D,
                         cd,
                         smax_coord )
                
    pdf_ints = [ histlist[0].ComputeIntegral(), histlist[3].ComputeIntegral() ]
    
    
    
    
    if ROOT.gPad:
        ROOT.gPad.SetLogy(logy)
        if quantity != "E": ROOT.gPad.SetLogx(logx)
    if logy : histlist[0].SetMinimum(1e-8)

    histlist[0].SetStats(False)
    histlist[0].GetXaxis().SetTitle(qvals[-1])
    histlist[0].GetXaxis().SetRangeUser(qvals[1], qvals[2])
    if logy1 > 0 :
        histlist[0].GetYaxis().SetRangeUser(10**logy0, 10**logy1)
    histlist[0].Draw("L")
    maximum = histlist[0].GetMaximum()
    
    legendbox1 = [ qvals[3][0], qvals[3][1] + 0.07, qvals[3][2], qvals[3][3] ]
    legendbox2 = [ qvals[3][0], qvals[3][1],        qvals[3][2], qvals[3][1] + 0.07 ]
    legendbox3 = [ qvals[3][0], qvals[3][1] - 0.04, qvals[3][2], qvals[3][1] + 0.03 ]
    
    legend = ROOT.TLegend(*legendbox1)
    legend.AddEntry(histlist[0], pdf_infos[0][4] + " total","l")    
    parleg = ROOT.TLegend(*legendbox2)
    parleg.AddEntry("", "10^%i GeV, %i m, cos#theta: %.2f, cos#theta_{PMT}: %.2f" %(logE, D, cd, cos_pmt), "")
    parleg.SetMargin(0.05)
    parleg.SetBorderSize(0)
    parleg.SetFillColorAlpha(0, 0)
    intleg = ROOT.TLegend(*legendbox3)
    intleg.AddEntry("", "Sum %s: %.2f, sum %s: %.2f" %(pdf_infos[0][4], pdf_ints[0], pdf_infos[1][4], pdf_ints[1]), "")
    intleg.SetMargin(0.05)
    intleg.SetBorderSize(0)
    intleg.SetFillColorAlpha(0, 0)
    
    for ipdf in range(len(pdf_infos)):
        for i in range( pdf_infos[ipdf][3] ): 
            col = [get_color(pdf_infos[ipdf][0])[0], get_color(pdf_infos[ipdf][0])[1], get_color(pdf_infos[ipdf][0])[1]][i]
            sty = [1, 2, 1, 1,  2,  1, 0][i] # dashed = scattered, solid = direct
            ltext = ["" + pdf_infos[ipdf][4] + " total", "" + pdf_infos[ipdf][4] + " scattered", "" + pdf_infos[ipdf][4] + " direct"][i]
            
            histlist[ipdf*pdf_infos[0][3] + i].SetLineWidth(2)
            histlist[ipdf*pdf_infos[0][3] + i].SetLineStyle(sty)
            histlist[ipdf*pdf_infos[0][3] + i].SetLineColor(col)
            histlist[ipdf*pdf_infos[0][3] + i].Draw("Lsame")
            this_maximum = histlist[ipdf*pdf_infos[0][3] + i].GetMaximum()
            if this_maximum > maximum:
                maximum = this_maximum
        
            if ipdf*pdf_infos[0][3] + i != 0: legend.AddEntry(histlist[ipdf*pdf_infos[0][3] + i], ltext,"l")
    
    histlist[0].SetMaximum(maximum * 1.05)
    legend.Draw();
    parleg.Draw();
    intleg.Draw();
    
    with out:
      
       # create png in memory 
       image = ROOT.TImage.Create()
       image.FromPad( ROOT.gPad )
       x = array('l', [0])
       y = array('i', [0])
       image.GetImageBuffer(x,y, ROOT.TImage.kPng)
       s = string_at( x[0],y[0]) 
       img = IPython.display.Image( s, format='png' )
            
       display(img)
       del x,y,s,img    
    

In [18]:
iplot = interactive(plot_pdf,
         pdf0=['aanet','jpp','jpp_shower_max', 'jpp_elongated'],
         pdf1=['aanet','jpp','jpp_shower_max', 'jpp_elongated'],
         quantity=['E','D', 'cd', 'cos_pmt'],
         logE=(2.0,8.0), D=(2.0,1000), cd = (-1,1,0.02), cos_pmt=(-1.0,1,0.02),
         nbins=(10,1000),
         x0 = (-1, 1, 0.001), x1 = (-1, 1, 0.001),
         logy0 = (0.0, 7, 0.01), logy1 = (0.0, 7, 0.01),
         steps = (1, 100),
         elong_steps = (1, 100),
         blur = 0.0)

leftbox  = VBox( iplot.children[: int(len(iplot.children) / 2)])
rightbox = VBox( iplot.children[int(len(iplot.children) / 2) : -1] )
display( HBox([leftbox, rightbox]) )

out = iplot.children[-1]
out.layout = {
            'width': '700px',
            'height': '600px',
            'border': '3px solid blue'
            }
iplot
display(out)

Output(layout=Layout(border='3px solid blue', height='600px', width='700px'))